### Day 14

Indeed, more often in real life, we will have more than just one predictor (input) that influences the response variable, this case is known as multiple linear regression.

Suppose now we are interested in studying the relation between "mpg" ($y$) and predictors "cylinders" ($x_1$), "displacement" ($x_2$), "horsepower ($x_3$)", "weight ($x_4$)", and "acceleration ($x_5$)". This multiple regression can be then expressed as $$y_i = \beta_0+\beta_1x_{i1}+\beta_2x_{i2}+\beta_3x_{i3}+\beta_4x_{i4}+\beta_5x_{i5}+\varepsilon_i$$

And the assumptions are the same as those for simple linear regression, namely, L.I.N.E.

The model fitting using Python packages is similar to what we have done last time.

In [ ]:
import pandas as pd
from sklearn.linear_model import LinearRegression

autos = pd.read_csv("https://users.pfw.edu/yorgovd/DM2/auto_all.csv", na_values="?")
print(any(autos.isna()))    # remember that we change "?" in "horsepower" variable to NaN - project 10

autos.dropna(inplace=True)  # remove the rows contain NaN

x = autos.loc[:, ['cylinders', 'displacement', 'horsepower', 'weight', 'acceleration']]
y = autos['mpg']

reg = LinearRegression().fit(x, y)
print(reg.intercept_,reg.coef_)
reg

Note that we can also write the same model using matrix notation: 
$$\mathbf{y} = \mathbf{X}\boldsymbol{\beta}+\boldsymbol{\varepsilon}$$

where
$$\mathbf{y}=\left(\begin{matrix}y_1 \\ y_2 \\ y_3 \\ \vdots \\ y_n \end{matrix}\right) \qquad \qquad \mathbf{X}=\left(\begin{matrix} 1 & x_{11} & x_{12} & \dots & x_{15} \\ 1 & x_{21} & x_{22} & \dots & x_{25} \\ 1 & x_{31} & x_{32} & \dots & x_{35} \\ \vdots & \vdots & \vdots & \ddots & \vdots \\ 1 & x_{n1} & x_{n2} & \dots & x_{n5}\end{matrix}\right) \qquad \qquad \boldsymbol{\beta}=\left(\begin{matrix}\beta_0 \\ \beta_1 \\ \beta_2 \\ \vdots \\ \beta_5 \end{matrix}\right) \qquad \qquad \boldsymbol{\varepsilon}=\left(\begin{matrix}\varepsilon_1 \\ \varepsilon_2 \\ \varepsilon_3 \\ \vdots \\ \varepsilon_n \end{matrix}\right)$$

It can be shown that, if the goal is to minimize the sum of squared errors like here, ($\boldsymbol{\varepsilon}'\boldsymbol{\varepsilon}$), 
we can obtain the estimate with matrix algrebgra only : $\hat{\boldsymbol{\beta}}=\left(\mathbf{X'X}\right)^{-1}\mathbf{X'y}$.

Let's fit with the model with linear algrebra next.

In [ ]:
# Computing the estimates using matrix formula

import statsmodels.api as sm
import numpy as np

X = np.array(sm.add_constant(x))    # convert DataFrame to numpy array for computation after adding the intercept column
y = np.array(y)

np.matmul(np.matmul(np.linalg.inv(np.matmul(np.transpose(X), X)), np.transpose(X)), y)  # compute beta using matrix formula

Going back to our model fit with *scikit-learn*, it returns an object with methods so one can use prediction using the model, similar to that in simple linear regression.

In [ ]:
pred = reg.predict(autos.iloc[:, 2:7])  # compute all predicted responses in the DataFrame
print(pred[0:5])   # showing only the first 5 predicted responses
# what are the actual values?

# what are the errors (residuals)?

In actuality, before one settles on a model, one must do variable selection, work to avoid overfitting (I recommend 10-fikd cross validation), etc. We don't have time for anything like this in this 1-credit class with the goal to get you started with Python. 

Importantly, once you have settled on a model available, the next step is often to check if the model actually meets the L.I.N.E. assumptions. Severe violation of the assumptions will weaken the power of inference/prediction based on the model. This does not address model selection, overfitting, etc. This step, diagnostic analysis is however crucial for any model-candidate. This often starts with producing plots based on the residuals of the regression model.

Below are the two commonly used plots for diagnosis purpose:

1. The plot of residual vs. predicted response tells us if linearity, independence and equal variance assumptions are approximately satisfied. The ideal pattern of the plot is that the points randomly scatter above and below the 0 horizontal line, forming a horizontal band of equal width.
2. The Q-Q plot of standardized residual tells us if the normality assumption is approximately satisfied. The ideal pattern is that the points should follow the straight line.

In [ ]:
import matplotlib.pyplot as plt
# we store the residuals
residual = y - pred

plt.figure(figsize=(12, 9))
plt.scatter(pred, residual, c='k')      # plot the residuals vs. predicted responses
plt.hlines([0,0], xmin=5, xmax=35)      # draw a horizontal line at 0
plt.show()

This plot indicates that linearity and equal variance assumptions may be violated, as all the points do not form a horizonal band, and the width of the band seems to become wider as we move from left to right. Some remedy measures we might able to take in order to correct these violations include:

1. transform response variable and/or predictor variables
2. include higher order term(s) (quadratic or interaction terms) in the regression equation
3. remove input variables/predictors that might be correlated.

More such details are discussed in STAT 51200 - Applied Regression Analysis, which is offered every fall semester.

A very commonly used diagnostic plot is the QQ-plot, plotting actual normal distribution quantiles against the sample quantiles.

In [ ]:
import statsmodels.formula.api as smf


reg2 = smf.ols('mpg~cylinders+displacement+horsepower+weight+acceleration', data=autos).fit()
std_res = reg2.get_influence().resid_studentized_internal     # obtain the standardized residuals

fig = sm.qqplot(std_res, line='45')     # produce the Q-Q normal plot
fig.set_size_inches(12, 9)              # resize the plot
plt.show()

This plot indicates the normal assumption is approximately met, as the majority of the points follow the straight line, only a few points lie a little away from the line.

We can also obtain a summary about the multiple regression model using the code below. Based on the output, it seems that "horsepower" and "weight" are the two significant predictors of "mpg" and their respective p-values are less than $\alpha=0.05$, while others are not. This may suggest that our final regression model for predicting auto "mpg" could avoid overfitting if onl only involve these two predictor variables. One simple regression 

In [ ]:
reg2.summary()

### Your tasks in this project

1. Know how to fit multiply regression model, obtain the regression equation and predict the response when values for predictor variables are given.
2. Realize that we only touched the topic of regression diagonstics.
3. (if time permits) Let's modify the code avobe to include only the two preditcors mentioned. Adjusted-$R^2$ adjusts for number of variables in the model. Is this higher for the new model?